In [2]:
import pandas as pd
import datetime as dt
import geopandas as gpd
import folium
import branca.colormap as cm
from folium.plugins import TimestampedGeoJson
#from folium.features import GeoJsonPopup, GeoJsonTooltip

In [3]:
#Reading json file
bikedata=pd.read_json('./stationsMonday.json')

In [4]:
#Dict with column names 
df={'date':[],'station':[],'occupancy':[],'capacity':[],'long':[],'lat':[]}
df

{'date': [],
 'station': [],
 'occupancy': [],
 'capacity': [],
 'long': [],
 'lat': []}

In [5]:
for _,row in bikedata.iterrows():
    for item in row:
        for cell in item['data']: 
            #print(cell['date'])
            df['occupancy'].append(cell['occupancy'])
            df['capacity'].append(cell['capacity'])
            df['date'].append(cell['date'])
            df['station'].append(item['id'])
            #print(cell['date'],item['coord']['lon'],item['coord']['lat'])
            df['long'].append(item['coord']['lon'])
            df['lat'].append(item['coord']['lat'])


In [6]:
#Setting up dataframe from dict and fix formatting on timestamp. 
data=pd.DataFrame.from_dict(df)
data['date']= pd.to_datetime(df['date'],unit='s')
temp=data
data['date']=data['date'].dt.strftime('%Y-%m-%dT%H:%M:%S')
data=data.sort_values(by='date')
data

date                               station  occupancy  \
0      2022-05-22T23:00:01  003b4566-1a1d-4aa5-9b2c-35972a0ac219          0   
4154   2022-05-22T23:00:01  539a3950-3996-453a-a9a9-ab276dc1c00f          0   
7595   2022-05-22T23:00:01  907dcd54-cdd9-4521-975e-b60cee9da28c          0   
1240   2022-05-22T23:00:01  1c887652-e924-4f34-b568-e4567ed10926          0   
10230  2022-05-22T23:00:01  e55d9f5f-cff5-445d-a72d-dd8ce1473514          0   
...                    ...                                   ...        ...   
7904   2022-05-24T13:30:01  90beb6ce-1e2b-4586-9514-4cd9ef0aff7c          1   
8059   2022-05-24T13:30:01  a679c4c4-01e6-4c44-9cb7-13b2c34ecbc2          0   
8214   2022-05-24T13:30:01  af8c27f2-b431-42cc-b659-46ae4922097f          2   
5579   2022-05-24T13:30:01  691d4e1c-0620-47ee-a5cd-901df077e3d0          0   
11469  2022-05-24T13:30:01  ffb197fc-9534-42eb-8090-6ff4ccecf7f3          0   

       capacity       long        lat  
0            12  17.993884  59.324599  
4154         10  18.075406  59.323144  
7595          5  18.031835  59.318370  
1240         16  18.036443  59.333875  
10230        16  18.056125  59.343615  
...         ...        ...        ...  
7904         10  18.098270  59.308706  
8059         11  18.091972  59.342983  
8214         12  18.018387  59.328284  
5579         14  18.051044  59.343040  
11469        16  18.070286  59.341596  

[11470 rows x 6 columns]

In [7]:
temp

date                               station  occupancy  \
0      2022-05-22T23:00:01  003b4566-1a1d-4aa5-9b2c-35972a0ac219          0   
1      2022-05-22T23:15:00  003b4566-1a1d-4aa5-9b2c-35972a0ac219          0   
2      2022-05-22T23:30:01  003b4566-1a1d-4aa5-9b2c-35972a0ac219          0   
3      2022-05-22T23:45:01  003b4566-1a1d-4aa5-9b2c-35972a0ac219          0   
4      2022-05-23T00:00:01  003b4566-1a1d-4aa5-9b2c-35972a0ac219          0   
...                    ...                                   ...        ...   
11465  2022-05-24T12:30:00  ffb197fc-9534-42eb-8090-6ff4ccecf7f3          0   
11466  2022-05-24T12:45:00  ffb197fc-9534-42eb-8090-6ff4ccecf7f3          0   
11467  2022-05-24T13:00:00  ffb197fc-9534-42eb-8090-6ff4ccecf7f3          0   
11468  2022-05-24T13:15:00  ffb197fc-9534-42eb-8090-6ff4ccecf7f3          0   
11469  2022-05-24T13:30:01  ffb197fc-9534-42eb-8090-6ff4ccecf7f3          0   

       capacity       long        lat  
0            12  17.993884  59.324599  
1            12  17.993884  59.324599  
2            12  17.993884  59.324599  
3            12  17.993884  59.324599  
4            12  17.993884  59.324599  
...         ...        ...        ...  
11465        16  18.070286  59.341596  
11466        16  18.070286  59.341596  
11467        16  18.070286  59.341596  
11468        16  18.070286  59.341596  
11469        16  18.070286  59.341596  

[11470 rows x 6 columns]

In [8]:
#Add stationnumber as a new column to dataframe
uniquestations={}
for row in enumerate(data['station'].unique()):
    uniquestations[str(row[1])]=row[0]+1
for index,row in data.iterrows():
    data.loc[data['station']==row['station'],'stationnr']=uniquestations[row['station']]




In [9]:
#Setting the status colors for occupancy dependent on capacity.
""" colorbar = cm.StepColormap(colors=['#15B01A','#FFA500','#FF7F00','#FF4500','#8B0000'], vmin=0,vmax=1)
data['color']=list(colorbar(x/y) for x,y in zip(data['occupancy'],data['capacity'])) """

" colorbar = cm.StepColormap(colors=['#15B01A','#FFA500','#FF7F00','#FF4500','#8B0000'], vmin=0,vmax=1)\ndata['color']=list(colorbar(x/y) for x,y in zip(data['occupancy'],data['capacity'])) "

In [10]:
#Need to fix a better looking colorbar with even steps and ticks that names the intervals correct. 
colorbar = cm.StepColormap(colors=['#EEE9E9','#00FF7F','#FFFF00','#FFA500','#FF8000','#C76114','#8B4500','#EE0000'],index=[0,0.2,1.1,2.1,3.1,5.1,7.1,10,100], vmin=0,vmax=100)

data['color']=list(colorbar(occupancy) for occupancy in data['occupancy'])
colorbar

In [11]:
colorbardisplayed = cm.StepColormap(colors=['#EEE9E9','#00FF7F','#FFFF00','#FFA500','#FF8000','#C76114','#8B4500','#EE0000'],index=[0,0.2,1.1,2.1,3.1,5.1,7.1,10], vmin=0,vmax=10,caption='Colorbar')
colorbardisplayed

In [16]:
#Adjusting size of markers dependant of occupancy
def setradius(size):
    radius=1 if size < 1 else 4
    return(radius)

def setopacity(size):
    opacity=0.4 if size<1 else 1
    return(opacity)

In [24]:
features = [{'type': 'Feature',
            'geometry': {'type':'Point', 'coordinates':[row['long'],row['lat']]},
            'properties': {'time': row['date'],
                           'popup':'Station: '+str(row['stationnr'])+'Occupancy: '+str(row['occupancy'])+'/'+str(row['capacity']),
                           'style': {'color' : ''},
                           'icon': 'circle',
                           'iconstyle':{'fillColor': row['color'],
                                        'fillOpacity': 1,
                                        'stroke': 'true',
                                        #'radius': setradius(row['occupancy'])}}
                                        'radius': 5}}
            } for _,row in data.iterrows()]

In [29]:
fig=folium.Figure(width=1200,height=700)
map = folium.Map(location = [59.32760990395156, 18.06760960579676], tiles='Stamen Toner' , zoom_start = 13).add_to(fig)
TimestampedGeoJson( features,
                            add_last_point = True,
                           period='PT15M',
                           loop_button=True,
                           time_slider_drag_update=True,
                           transition_time = 50,
                           
                           
                            ).add_to(map)
map.add_child(colorbardisplayed)
fig


In [28]:
map.save('index.html')